In [1]:
# imports 
import numpy as np

#### Opent the file and create 3 dictionaries for each data file

In [2]:
# Open the data and create 3 dictionaries where the keys are the sentance id and the 
# values are the words with the lables 
def parse_iob2_content(content):
    data = {}
    sentence_id = None
    for line in content.split('\n'):
        line = line.strip()
        if line.startswith('# sent_id ='):
            sentence_id = line.split('=')[1].strip()
            data[sentence_id] = []
        elif line and not line.startswith('#'):
            parts = line.split('\t')
            data[sentence_id].append((parts[1], parts[2]))
    return data

# Parse training data
with open('en_ewt-ud-train.iob2', 'r', encoding='utf-8') as file:
    content_train = file.read()

data_train = parse_iob2_content(content_train)

# Parse development data
with open('en_ewt-ud-dev.iob2', 'r', encoding='utf-8') as file:
    content_dev = file.read()

data_dev = parse_iob2_content(content_dev)

# Parse test data
with open('en_ewt-ud-test-masked.iob2', 'r', encoding='utf-8') as file:
    content_test = file.read()

data_test = parse_iob2_content(content_test)



In [3]:
# Print the training data dictionary
print("----- Training Data -----")
for key, value in data_train.items():
    print(key, value)

----- Training Data -----
answers-20090605110235AAALlCt_ans-0001 [('Where', 'O'), ('in', 'O'), ('the', 'O'), ('world', 'O'), ('is', 'O'), ('Iguazu', 'B-LOC'), ('?', 'O')]
answers-20090605110235AAALlCt_ans-0002 [('Iguazu', 'B-LOC'), ('Falls', 'I-LOC')]
answers-20090605110235AAALlCt_ans-0003 [('Widely', 'O'), ('considered', 'O'), ('to', 'O'), ('be', 'O'), ('one', 'O'), ('of', 'O'), ('the', 'O'), ('most', 'O'), ('spectacular', 'O'), ('waterfalls', 'O'), ('in', 'O'), ('the', 'O'), ('world', 'O'), (',', 'O'), ('the', 'O'), ('Iguazu', 'B-LOC'), ('Falls', 'I-LOC'), ('on', 'O'), ('the', 'O'), ('border', 'O'), ('of', 'O'), ('Argentina', 'B-LOC'), ('and', 'O'), ('Brazil', 'B-LOC'), (',', 'O'), ('are', 'O'), ('a', 'O'), ('certainly', 'O'), ('must', 'O'), ('see', 'O'), ('attraction', 'O'), ('in', 'O'), ('the', 'O'), ('area', 'O'), ('.', 'O')]
answers-20090605110235AAALlCt_ans-0004 [('The', 'O'), ('centre', 'O'), ('of', 'O'), ('the', 'O'), ('falls', 'O'), ('is', 'O'), ('known', 'O'), ('locally', 'O

In [4]:

# Collect unique labels
unique_labels = set()
for key, value in data_train.items():
    for _, label in value:
        unique_labels.add(label)

# Print unique labels
#print("Unique labels:", unique_labels)

# Convert set to list
unique_labels_list = list(unique_labels)

# Add 'PAD' at the beginning of the list
unique_labels_list.insert(0, 'PAD')

print(unique_labels_list)



['PAD', 'I-ORG', 'B-PER', 'B-LOC', 'I-PER', 'I-LOC', 'B-ORG', 'O']


#### Create the labled matrix 

In [5]:
# Find the max sentance (number of rows)
# Initialize variables to store the longest sentence and its length
longest_sentence = []
max_length = 0

# Iterate through the data to find the longest sentence
for key, sentence in data_train.items():
    sentence_length = len(sentence)
    if sentence_length > max_length:
        max_length = sentence_length
        longest_sentence = sentence

# Print the longest sentence and its length
print("Longest sentence:", longest_sentence)
print("Length of longest sentence:", max_length)
# ID of the sentance: 
# ID of longest sentence: newsgroup-groups.google.com_alt.animals_434fe80fb3577e8e_ENG_20031011_200300-0020

Longest sentence: [('Antichrist', 'O'), ('John', 'B-PER'), ('Lennon', 'I-PER'), ('wanted', 'O'), ('to', 'O'), ('compete', 'O'), ('with', 'O'), ('Jesus', 'B-PER'), ('Christ', 'I-PER'), (',', 'O'), ('and', 'O'), ('so', 'O'), ('he', 'O'), ('grew', 'O'), ('a', 'O'), ('beard', 'O'), ('and', 'O'), ('started', 'O'), ('to', 'O'), ('make', 'O'), ('a', 'O'), ('bogus', 'O'), ('role', 'O'), ('of', 'O'), ('Christ', 'B-PER'), ('together', 'O'), ('with', 'O'), ('Yoko', 'B-PER'), ('Ono', 'I-PER'), ('at', 'O'), ('the', 'O'), ('Amsterdam', 'B-LOC'), ('Hilton', 'I-LOC'), ('hotel', 'I-LOC'), ('proclaiming', 'O'), ('"', 'O'), ('Peace', 'O'), ('"', 'O'), (',', 'O'), ('being', 'O'), ('then', 'O'), ('when', 'O'), ('he', 'O'), ('was', 'O'), ('visited', 'O'), ('by', 'O'), ('the', 'O'), ('Canadian', 'O'), ('journalist', 'O'), ('who', 'O'), ('ridiculized', 'O'), ('and', 'O'), ('admonished', 'O'), ('him', 'O'), ('wanting', 'O'), ('to', 'O'), ('know', 'O'), ('about', 'O'), ('what', 'O'), ('Lennon', 'B-PER'), ('mean

In [6]:
# Find the number of sentance (numb of columns)
# Count the number of keys in the dictionary
num_keys = len(data_train)

# Print the number of keys
print("Number of keys:", num_keys)


Number of keys: 12543


In [7]:
# Create the matrix
# Define the dimensions of the matrix
num_rows = 159
num_columns = 12543

# Create a matrix filled with zeros
zero_matrix = np.zeros((num_rows, num_columns))

# Print the shape of the matrix
print("Shape of the zero matrix:", zero_matrix.shape)


Shape of the zero matrix: (159, 12543)


In [8]:
# Function to create matrices for sentences and labels
def create_matrices(data):
    # Extract sentences and labels
    sentences = []
    labels = []

    for sentence_id, value in data.items():
        sentence = [word[0] for word in value]
        label = [word[1] for word in value]
        sentences.append(sentence)
        labels.append(label)

    # Find the maximum sentence length
    max_sentence_length = max(len(sentence) for sentence in sentences)

    # Create matrices for sentences and labels
    sentence_matrix = np.zeros((len(sentences), max_sentence_length), dtype=object)
    label_matrix = np.zeros((len(sentences), max_sentence_length), dtype=object)

    # Fill the matrices
    for i, (sentence, label) in enumerate(zip(sentences, labels)):
        sentence_matrix[i, :len(sentence)] = sentence
        label_matrix[i, :len(label)] = label

    return sentence_matrix, label_matrix

# Parse training data
with open('en_ewt-ud-train.iob2', 'r', encoding='utf-8') as file:
    content_train = file.read()

# Parse the content to create data_train dictionary
data_train = parse_iob2_content(content_train)

# Create matrices for sentences and labels
sentence_matrix, label_matrix = create_matrices(data_train)

# Print the shape of the matrices
print("Shape of the sentence matrix:", sentence_matrix.shape)
print("Shape of the label matrix:", label_matrix.shape)

# Print the matrices
print("Sentence Matrix:")
print(sentence_matrix)
#print("\nLabel Matrix:")
#print(label_matrix)

Shape of the sentence matrix: (12543, 159)
Shape of the label matrix: (12543, 159)
Sentence Matrix:
[['Where' 'in' 'the' ... 0 0 0]
 ['Iguazu' 'Falls' 0 ... 0 0 0]
 ['Widely' 'considered' 'to' ... 0 0 0]
 ...
 ['The' 'urge' 'to' ... 0 0 0]
 ['Take' 'care' ',' ... 0 0 0]
 ['I' "'m" 'sorry' ... 0 0 0]]


In [9]:
# For labled matrix 
#['PAD', 'B-PER', 'I-ORG', 'B-LOC', 'B-ORG', 'O', 'I-PER', 'I-LOC']

In [10]:
# Provided labels
provided_labels = ['PAD', 'B-PER', 'I-ORG', 'B-LOC', 'B-ORG', 'O', 'I-PER', 'I-LOC']

# Create a dictionary to map labels to indices
label_to_index = {label: index for index, label in enumerate(provided_labels)}

# Function to map labels to indices
def map_label_to_index(label):
    if label in label_to_index:
        return label_to_index[label]
    else:
        return label_to_index['PAD']

# Create a new matrix to store the indices
mapped_label_matrix = np.zeros_like(label_matrix, dtype=int)

# Loop through the label matrix and map labels to indices
for i in range(label_matrix.shape[0]):
    for j in range(label_matrix.shape[1]):
        mapped_label_matrix[i, j] = map_label_to_index(label_matrix[i, j])

# Print the mapped label matrix
print("Mapped Label Matrix:")
print(mapped_label_matrix[0])


Mapped Label Matrix:
[5 5 5 5 5 3 5 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0]


In [11]:
# Initialize an empty set to store unique words
unique_words = set()

# Loop through the sentence matrix and add non-zero elements to the set
for sentence in sentence_matrix:
    for word in sentence:
        if word != 0:  # Exclude padding
            unique_words.add(word)

# Print the set of unique words
print("Set of unique words:", unique_words)


Set of unique words: {'assumption', 'Nordstrom', 'anti', 'controversial', 'Asi', 'Theory', 'thankfully', 'disastrous', 'talkshow', 'United', 'Feith', 'amphibious', 'politely', 'Armed', 'Aerocom', 'Switchboard', 'clothes', 'CA', 'petco', 'Breeding', 'declaring', 'went', 'engineers', 'Aesthetics', 'contaminated', 'effected', 'vacuous', 'reprisal', 'haircut', 'perv', 'ekrapels@esaibos.com', 'launch', 'potpourri', 'curves', 'grim', 'advises', 'haircuts', 'easy', 'select', 'Vajpayee', 'antichrist', 'Hoax', 'Im', 'hissy', '376-9004', 'believe', 'Stanford', 'Bio', 'overdue', 'cargo', 'Futurism', 'solicit', 'switched', 'Warning', 'Ulistic', 'Atef', 'ramp', 'eatables', '45', 'spike', 'dab', 'NEEEEEEEEEVERRRR', 'sum', 'shrubs', 'eleven', 'Lucas', 'Similarly', 'http://www.thetruthseeker.co.uk/article.asp?id=4503', 'editorial', 'migrated', 'public', '+++', 'mormon', 'Derivatives', 'unspoken', 'Came', 'Andy', 'tick', 'testosterone', 'Thank', 'Jeremy', 'Rebecca', 'congratulated', 'Nope', 'motivation

In [19]:
# Convert the set of unique words to a list
unique_words_list = list(unique_words)

# Print the list of unique words
print("List of unique words:", unique_words_list)
print(len(unique_words_list))

List of unique words: ['assumption', 'Nordstrom', 'anti', 'controversial', 'Asi', 'Theory', 'thankfully', 'disastrous', 'talkshow', 'United', 'Feith', 'amphibious', 'politely', 'Armed', 'Aerocom', 'Switchboard', 'clothes', 'CA', 'petco', 'Breeding', 'declaring', 'went', 'engineers', 'Aesthetics', 'contaminated', 'effected', 'vacuous', 'reprisal', 'haircut', 'perv', 'ekrapels@esaibos.com', 'launch', 'potpourri', 'curves', 'grim', 'advises', 'haircuts', 'easy', 'select', 'Vajpayee', 'antichrist', 'Hoax', 'Im', 'hissy', '376-9004', 'believe', 'Stanford', 'Bio', 'overdue', 'cargo', 'Futurism', 'solicit', 'switched', 'Warning', 'Ulistic', 'Atef', 'ramp', 'eatables', '45', 'spike', 'dab', 'NEEEEEEEEEVERRRR', 'sum', 'shrubs', 'eleven', 'Lucas', 'Similarly', 'http://www.thetruthseeker.co.uk/article.asp?id=4503', 'editorial', 'migrated', 'public', '+++', 'mormon', 'Derivatives', 'unspoken', 'Came', 'Andy', 'tick', 'testosterone', 'Thank', 'Jeremy', 'Rebecca', 'congratulated', 'Nope', 'motivatio

In [13]:
# Create a new matrix to store the indices of unique words
word_index_matrix = np.zeros_like(sentence_matrix, dtype=int)

# Create a dictionary to map words to their indices in the list of unique words
word_to_index = {word: index for index, word in enumerate(unique_words_list)}

# Loop through the sentence matrix and replace words with their indices
for i in range(sentence_matrix.shape[0]):
    for j in range(sentence_matrix.shape[1]):
        word = sentence_matrix[i, j]
        if word != 0:  # Exclude padding
            word_index_matrix[i, j] = word_to_index[word]

# Print the matrix with word indices
print("Matrix with word indices:")
print(word_index_matrix[0])


Matrix with word indices:
[11537  4817 14482  6676   221 13851  8725     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0]


In [14]:
# check if it works
# Words to find
words_to_find = ['Where', 'in', 'the']

# Find indices of the words in the list of unique words
word_indices = {}
for word in words_to_find:
    index = unique_words_list.index(word)
    word_indices[word] = index

# Print the indices of the words
for word, index in word_indices.items():
    print(f"Index of '{word}': {index}")


Index of 'Where': 11537
Index of 'in': 4817
Index of 'the': 14482


In [15]:
import torch

# Convert matrices to tensor vectors
word_index_tensor = torch.tensor(word_index_matrix)
mapped_label_tensor = torch.tensor(mapped_label_matrix)

# Print the shapes of the tensor vectors
print("Shape of word_index_tensor:", word_index_tensor.shape)
print("Shape of mapped_label_tensor:", mapped_label_tensor.shape)


Shape of word_index_tensor: torch.Size([12543, 159])
Shape of mapped_label_tensor: torch.Size([12543, 159])


In [18]:
import torch
import torch.nn as nn
import torch.optim as optim

# Define a simple BiLSTM model
class BiLSTM(nn.Module):
    def __init__(self, input_dim, embedding_dim, hidden_dim, output_dim):
        super(BiLSTM, self).__init__()
        self.embedding = nn.Embedding(input_dim, embedding_dim)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim, bidirectional=True)
        self.fc = nn.Linear(hidden_dim * 2, output_dim)

    def forward(self, text):
        embedded = self.embedding(text)
        lstm_output, _ = self.lstm(embedded)
        predictions = self.fc(lstm_output)
        return predictions

# Dummy parameters for testing
input_dim = 19673  # Number of unique words in the vocabulary
embedding_dim = 100  # Dimension of word embeddings??
hidden_dim = 32  # Dimension of hidden states in the LSTM??
output_dim = 8  # Number of output labels

# Dummy word_index_matrix and mapped_label_matrix
word_index_matrix = torch.randint(0, input_dim, (100, 20))  # Example shape: (num_sentences, max_sentence_length)
mapped_label_matrix = torch.randint(0, output_dim, (100, 20))  # Example shape: (num_sentences, max_sentence_length)

# Initialize the model
model = BiLSTM(input_dim, embedding_dim, hidden_dim, output_dim)

# Dummy training loop
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters())

num_epochs = 2
for epoch in range(num_epochs):
    optimizer.zero_grad()
    predictions = model(word_index_matrix)
    predictions_flattened = predictions.view(-1, output_dim)
    labels_flattened = mapped_label_matrix.view(-1)
    loss = criterion(predictions_flattened, labels_flattened)
    loss.backward()
    optimizer.step()
    print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item()}')


Epoch [1/2], Loss: 2.088277578353882
Epoch [2/2], Loss: 2.085602283477783
